In [1]:
from pyspark import SparkContext, SparkConf
cf = SparkConf()
cf.set("spark.submit.deployMode","client")
sc = SparkContext.getOrCreate(cf)
from pyspark.sql import SparkSession
spark = SparkSession \
	    .builder \
	    .appName("TransitTrends- Taxi") \
	    .config("spark.some.config.option", "some-value") \
	    .getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/05/07 17:55:03 INFO org.apache.spark.SparkEnv: Registering MapOutputTracker
23/05/07 17:55:03 INFO org.apache.spark.SparkEnv: Registering BlockManagerMaster
23/05/07 17:55:03 INFO org.apache.spark.SparkEnv: Registering BlockManagerMasterHeartbeat
23/05/07 17:55:03 INFO org.apache.spark.SparkEnv: Registering OutputCommitCoordinator


In [2]:
import os
from sodapy import Socrata
import pandas as pd
import numpy as np

### Loading All datasets

In [4]:
import subprocess
# downloading Yellow cab data(2019-2022) from site https://www.nyc.gov/site/tlc/about/tlc-trip-record-data.page
url = "https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_20"
output_dir = "/home/sk9944_nyu_edu/TAXI/YELLOW_CABS/"
#clearing output folder to avoid downloading duplicates:
subprocess.call(["rm", "-rf", output_dir])
subprocess.call(["mkdir", output_dir])
for i in range(19,23):
    for j in range(1, 13):
        url_1 = str(j)
        if j<10:
            url_1 = "0"+url_1
        print("wget "+ url+str(i)+"-"+url_1+".parquet")
        # Run wget command
        subprocess.call(["wget", "-P", output_dir, url+str(i)+"-"+url_1+".parquet"])

wget https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2019-01.parquet


--2023-05-07 18:03:37--  https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2019-01.parquet
Resolving d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)... 18.160.201.5, 18.160.201.50, 18.160.201.126, ...
Connecting to d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)|18.160.201.5|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 110439634 (105M) [application/x-www-form-urlencoded]
Saving to: ‘/home/sk9944_nyu_edu/TAXI/YELLOW_CABS/yellow_tripdata_2019-01.parquet’

     0K .......... .......... .......... .......... ..........  0% 5.57M 19s
    50K .......... .......... .......... .......... ..........  0% 5.92M 18s
   100K .......... .......... .......... .......... ..........  0% 14.5M 15s
   150K .......... .......... .......... .......... ..........  0% 13.0M 13s
   200K .......... .......... .......... .......... ..........  0% 15.4M 12s
   250K .......... .......... .......... .......... ..........  0% 19.1M 11s
   300K .

wget https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2019-02.parquet


...... .......... 13%  364M 1s
 13550K .......... .......... .......... .......... .......... 13%  235M 1s
 13600K .......... .......... .......... .......... .......... 13%  274M 1s
 13650K .......... .......... .......... .......... .......... 13%  296M 1s
 13700K .......... .......... .......... .......... .......... 13%  381M 1s
 13750K .......... .......... .......... .......... .......... 13%  402M 1s
 13800K .......... .......... .......... .......... .......... 13%  172M 1s
 13850K .......... .......... .......... .......... .......... 13%  364M 1s
 13900K .......... .......... .......... .......... .......... 13%  383M 1s
 13950K .......... .......... .......... .......... .......... 13%  375M 1s
 14000K .......... .......... .......... .......... .......... 13%  353M 1s
 14050K .......... .......... .......... .......... .......... 13%  358M 1s
 14100K .......... .......... .......... .......... .......... 14%  408M 1s
 14150K .......... .......... .......... .......... .....

wget https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2019-03.parquet


...

.. .......... .......... .......... 23%  132M 0s
 13350K .......... .......... .......... .......... .......... 24%  117M 0s
 13400K .......... .......... .......... .......... .......... 24%  176M 0s
 13450K .......... .......... .......... .......... .......... 24%  137M 0s
 13500K .......... .......... .......... .......... .......... 24%  165M 0s
 13550K .......... .......... .......... .......... .......... 24%  167M 0s
 13600K .......... .......... .......... .......... .......... 24%  148M 0s
 13650K .......... .......... .......... .......... .......... 24%  129M 0s
 13700K .......... .......... .......... .......... .......... 24%  200M 0s
 13750K .......... .......... .......... .......... .......... 24%  161M 0s
 13800K .......... .......... .......... .......... .......... 24%  147M 0s
 13850K .......... .......... .......... .......... .......... 24%  187M 0s
 13900K .......... .......... .......... .......... .......... 25%  132M 0s
 13950K .......... .......... .........

wget https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2022-11.parquet


.. .......... .......... .......... .......... 27%  106M 0s
 13250K .......... .......... .......... .......... .......... 27%  388M 0s
 13300K .......... .......... .......... .......... .......... 27% 74.3M 0s
 13350K .......... .......... .......... .......... .......... 27%  360M 0s
 13400K .......... .......... .......... .......... .......... 27%  257M 0s
 13450K .......... .......... .......... .......... .......... 27%  383M 0s
 13500K .......... .......... .......... .......... .......... 27%  383M 0s
 13550K .......... .......... .......... .......... .......... 27%  159M 0s
 13600K .......... .......... .......... .......... .......... 27%  331M 0s
 13650K .......... .......... .......... .......... .......... 27%  395M 0s
 13700K .......... .......... .......... .......... .......... 28%  315M 0s
 13750K .......... .......... .......... .......... .......... 28%  261M 0s
 13800K .......... .......... .......... .......... .......... 28%  279M 0s
 13850K .......... .........

wget https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2022-12.parquet


.... .......... .......... .......... 31%  262M 0s
 16400K .......... .......... .......... .......... .......... 31%  263M 0s
 16450K .......... .......... .......... .......... .......... 31%  258M 0s
 16500K .......... .......... .......... .......... .......... 31%  328M 0s
 16550K .......... .......... .......... .......... .......... 31%  275M 0s
 16600K .......... .......... .......... .......... .......... 31%  264M 0s
 16650K .......... .......... .......... .......... .......... 31%  318M 0s
 16700K .......... .......... .......... .......... .......... 31%  279M 0s
 16750K .......... .......... .......... .......... .......... 32%  335M 0s
 16800K .......... .......... .......... .......... .......... 32%  283M 0s
 16850K .......... .......... .......... .......... .......... 32%  285M 0s
 16900K .......... .......... .......... .......... .......... 32%  287M 0s
 16950K .......... .......... .......... .......... .......... 32%  256M 0s
 17000K .......... .......... .......

In [5]:
# downloading Green cab data(2019-2022) from site https://www.nyc.gov/site/tlc/about/tlc-trip-record-data.page
url = "https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_20"
output_dir = "/home/sk9944_nyu_edu/TAXI/GREEN_CABS/"
#clearing output folder to avoid downloading duplicates:
subprocess.call(["rm", "-rf", output_dir])
subprocess.call(["mkdir", output_dir])
for i in range(19,23):
    for j in range(1, 13):
        url_1 = str(j)
        if j<10:
            url_1 = "0"+url_1
        print("wget "+ url+str(i)+"-"+url_1+".parquet")
        # Run wget command
        subprocess.call(["wget", "-P", output_dir, url+str(i)+"-"+url_1+".parquet"])

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2019-01.parquet


--2023-05-07 18:04:22--  https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2019-01.parquet
Resolving d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)... 18.160.201.50, 18.160.201.5, 18.160.201.131, ...
Connecting to d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)|18.160.201.50|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 11071980 (11M) [binary/octet-stream]
Saving to: ‘/home/sk9944_nyu_edu/TAXI/GREEN_CABS/green_tripdata_2019-01.parquet’

     0K .......... .......... .......... .......... ..........  0% 4.29M 2s
    50K .......... .......... .......... .......... ..........  0% 4.33M 2s
   100K .......... .......... .......... .......... ..........  1% 9.62M 2s
   150K .......... .......... .......... .......... ..........  1% 10.0M 2s
   200K .......... .......... .......... .......... ..........  2% 9.67M 2s
   250K .......... .......... .......... .......... ..........  2% 15.5M 1s
   300K .......... .......... ...

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2019-02.parquet


........  0% 5.63M 2s
   100K .......... .......... .......... .......... ..........  1% 14.6M 1s
   150K .......... .......... .......... .......... ..........  1% 13.2M 1s
   200K .......... .......... .......... .......... ..........  2% 14.9M 1s
   250K .......... .......... .......... .......... ..........  2% 19.3M 1s
   300K .......... .......... .......... .......... ..........  3% 16.1M 1s
   350K .......... .......... .......... .......... ..........  3% 22.5M 1s
   400K .......... .......... .......... .......... ..........  4% 28.8M 1s
   450K .......... .......... .......... .......... ..........  4% 41.4M 1s
   500K .......... .......... .......... .......... ..........  5% 29.9M 1s
   550K .......... .......... .......... .......... ..........  5% 63.7M 1s
   600K .......... .......... .......... .......... ..........  6% 38.4M 1s
   650K .......... .......... .......... .......... ..........  6% 59.1M 1s
   700K .......... .......... .......... .......... ..........  7%

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2019-03.parquet


...

HTTP request sent, awaiting response... 200 OK
Length: 1346660 (1.3M) [binary/octet-stream]
Saving to: ‘/home/sk9944_nyu_edu/TAXI/GREEN_CABS/green_tripdata_2022-08.parquet’

     0K .......... .......... .......... .......... ..........  3% 5.58M 0s
    50K .......... .......... .......... .......... ..........  7% 4.93M 0s
   100K .......... .......... .......... .......... .......... 11% 14.2M 0s
   150K .......... .......... .......... .......... .......... 15% 9.46M 0s
   200K .......... .......... .......... .......... .......... 19% 15.6M 0s
   250K .......... .......... .......... .......... .......... 22% 13.0M 0s
   300K .......... .......... .......... .......... .......... 26% 21.2M 0s
   350K .......... .......... .......... .......... .......... 30% 21.2M 0s
   400K .......... .......... .......... .......... .......... 34% 40.0M 0s
   450K .......... .......... .......... .......... .......... 38% 48.9M 0s
   500K .......... .......... .......... .......... .......... 41%

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-09.parquet
wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-10.parquet


......... .......... .......... 21% 19.8M 0s
   300K .......... .......... .......... .......... .......... 24% 19.6M 0s
   350K .......... .......... .......... .......... .......... 28% 17.4M 0s
   400K .......... .......... .......... .......... .......... 31% 31.5M 0s
   450K .......... .......... .......... .......... .......... 35% 36.3M 0s
   500K .......... .......... .......... .......... .......... 38% 33.3M 0s
   550K .......... .......... .......... .......... .......... 42% 58.0M 0s
   600K .......... .......... .......... .......... .......... 46% 35.3M 0s
   650K .......... .......... .......... .......... .......... 49% 65.9M 0s
   700K .......... .......... .......... .......... .......... 53% 39.3M 0s
   750K .......... .......... .......... .......... .......... 56% 42.3M 0s
   800K .......... .......... .......... .......... .......... 60% 64.4M 0s
   850K .......... .......... .......... .......... .......... 63% 48.7M 0s
   900K .......... .......... .......... ..

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-11.parquet
wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-12.parquet


--2023-05-07 18:04:47--  https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-11.parquet
Resolving d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)... 18.160.201.50, 18.160.201.5, 18.160.201.131, ...
Connecting to d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)|18.160.201.50|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1270324 (1.2M) [binary/octet-stream]
Saving to: ‘/home/sk9944_nyu_edu/TAXI/GREEN_CABS/green_tripdata_2022-11.parquet’

     0K .......... .......... .......... .......... ..........  4% 6.17M 0s
    50K .......... .......... .......... .......... ..........  8% 5.34M 0s
   100K .......... .......... .......... .......... .......... 12% 4.90M 0s
   150K .......... .......... .......... .......... .......... 16% 14.5M 0s
   200K .......... .......... .......... .......... .......... 20% 12.5M 0s
   250K .......... .......... .......... .......... .......... 24% 22.3M 0s
   300K .......... .......... ...

In [6]:
local_directory_path = "/home/sk9944_nyu_edu/TAXI/"

# HDFS directory to copy the directory to
hdfs_directory_path = "/shared/TAXI"
hdfs_shared_path = "/shared/"

subprocess.call(["hdfs", "dfs", "-rm", "-r", hdfs_directory_path])

Deleted /shared/TAXI


0

In [7]:
subprocess.call(["hdfs", "dfs", "-put", local_directory_path, hdfs_shared_path])

0